### Load Pretrained Model and Dataset

- HLLM model from ByteDance (https://huggingface.co/ByteDance/HLLM)
- Amazon Books Review dataset (randomly select 50,000 items)

In [1]:
from transformers import AutoModel, AutoTokenizer

model_path = 'checkpoints'

tokenizer = AutoTokenizer.from_pretrained(model_path)

if tokenizer.pad_token is None:
    tokenizer.add_special_tokens({'pad_token': '[PAD]'})
    tokenizer.pad_token = '[PAD]'

model = AutoModel.from_pretrained(model_path)
model.resize_token_embeddings(len(tokenizer))


/home/fc2456/.local/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-12-14 15:14:23.065302: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1734207263.086446   31852 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1734207263.092826   31852 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-12-14 15:14:23.115110: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operation

Embedding(32001, 2048)

In [2]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split

interactions = pd.read_csv('dataset/filtered_amazon_books.csv')
information = pd.read_csv('information/amazon_books_reduced.csv')
merged_df = interactions.merge(information, on = 'item_id', how = 'inner')

# encode
merged_df['user_id'] = merged_df['user_id'].astype('category').cat.codes
merged_df['item_id'] = merged_df['item_id'].astype('category').cat.codes

train_data, test_data = train_test_split(merged_df, test_size=0.2, random_state=42)

In [3]:
# import requests

# url = "https://huggingface.co/ByteDance/HLLM/resolve/main/1B_books/pytorch_model.bin"
# save_path = "pytorch_model.bin"

# response = requests.get(url, stream=True)
# if response.status_code == 200:
#     with open(save_path, 'wb') as file:
#         for chunk in response.iter_content(chunk_size=1024):
#             file.write(chunk)
#     print(f"File downloaded successfully to {save_path}")
# else:
#     print(f"Failed to download file: {response.status_code}")

In [4]:
# train_data['description'] = train_data['description'].fillna('')
# train_data['description'] = train_data['description'].astype(str)

### Create RecSys model and dataloader

In [5]:
import torch
import torch.nn as nn
from transformers import AutoModel

device = 'cuda' if torch.cuda.is_available() else 'cpu'

class RecommendationModelWithHLLM(nn.Module):
    def __init__(self, hllm, num_users, num_items, embedding_dim=256):
        super(RecommendationModelWithHLLM, self).__init__()
        self.hllm = hllm  # Pretrained HLLM model
        self.user_embedding = nn.Embedding(num_users, embedding_dim)
        self.item_embedding = nn.Embedding(num_items, embedding_dim)

        # make embeddings to the same size as user/item embeddings
        self.metadata_projection = nn.Linear(hllm.config.hidden_size, embedding_dim)

        self.fc = nn.Linear(embedding_dim * 3, 1)

    def forward(self, user_ids, item_ids, item_metadata):
        # convert to LongTensor
        user_ids = user_ids.to(device).long()  
        item_ids = item_ids.to(device).long()  
        
        user_embeds = self.user_embedding(user_ids)  
        item_embeds = self.item_embedding(item_ids)  
        metadata_embeds = self.hllm(**item_metadata).last_hidden_state.mean(dim=1)  
        metadata_embeds = self.metadata_projection(metadata_embeds)  

        combined = torch.cat([user_embeds, item_embeds, metadata_embeds], dim=-1)  

        output = self.fc(combined)  
        return output


In [6]:
num_users = merged_df['user_id'].nunique()
num_items = merged_df['item_id'].nunique()
recommendation_model = RecommendationModelWithHLLM(model, num_users, num_items)

In [7]:
from torch.utils.data import DataLoader, Dataset

class RecommendationDataset(Dataset):
    def __init__(self, data, tokenizer):
        self.data = data
        self.tokenizer = tokenizer

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        row = self.data.iloc[idx]

        description = row['description'] if isinstance(row['description'], str) else str(row['description'])

        user_id = torch.tensor(row['user_id'])
        item_id = torch.tensor(row['item_id'])
        metadata = self.tokenizer(
            description,
            return_tensors='pt',
            truncation=True,
            padding=True
        )
        target = torch.tensor(row['timestamp']).float()  
        return user_id, item_id, metadata, target

In [8]:
def collate_fn(batch):
    user_ids = torch.stack([item[0] for item in batch])  
    item_ids = torch.stack([item[1] for item in batch])  
    targets = torch.stack([item[3] for item in batch])  

    metadata_batch = [item[2] for item in batch]  
    input_ids = [m["input_ids"].squeeze(0) for m in metadata_batch]
    attention_mask = [m["attention_mask"].squeeze(0) for m in metadata_batch]

    padded_metadata = {
        "input_ids": torch.nn.utils.rnn.pad_sequence(input_ids, batch_first=True, padding_value=tokenizer.pad_token_id),
        "attention_mask": torch.nn.utils.rnn.pad_sequence(attention_mask, batch_first=True, padding_value=0),
    }

    return user_ids, item_ids, padded_metadata, targets

# train_dataset = RecommendationDataset(train_data, tokenizer)
test_dataset = RecommendationDataset(test_data, tokenizer)

# train_loader = DataLoader(
#     train_dataset,
#     batch_size=8,
#     shuffle=True,
#     collate_fn=collate_fn
# )

test_loader = DataLoader(
    test_dataset,
    batch_size=8,
    shuffle=False,
    collate_fn=collate_fn
)

### Pruning

In [9]:
from torch.nn.utils import prune
from torch import nn

def apply_pruning(model, sparsity):
    for name, module in model.named_modules():
        if isinstance(module, nn.Linear):  # for fully connected layer 
            prune.l1_unstructured(module, name="weight", amount=sparsity)  
            prune.remove(module, 'weight')  
    return model

# sparsity ratios
#sparsity = 0.3  
#sparsity = 0.5
sparsity = 0.7
pruned_model = apply_pruning(recommendation_model, sparsity=sparsity)
if torch.cuda.device_count() > 1:
    pruned_model = nn.DataParallel(pruned_model)

### Evaluation
#### 1. latency

In [17]:
import time
from tqdm import tqdm
import gc  

def measure_latency(model, dataloader, device=device):
    model = model.to(device)
    model.eval()
    total_latency = 0.0
    num_batches = 0

    with torch.no_grad():
        for batch in tqdm(dataloader, desc="Measuring Latency", unit="batch"):
            try:
                user_ids = batch[0].to(device).long()
                item_ids = batch[1].to(device).long()
                item_metadata = {
                    "input_ids": batch[2]["input_ids"][:, :128].to(device),  
                    "attention_mask": batch[2]["attention_mask"][:, :128].to(device)
                }

                if torch.cuda.is_available():
                    torch.cuda.synchronize()
                start_time = time.time()

                # Forward pass
                _ = model(user_ids, item_ids, item_metadata)

                if torch.cuda.is_available():
                    torch.cuda.synchronize()
                end_time = time.time()
                
                total_latency += (end_time - start_time)
                num_batches += 1

            except RuntimeError as e:
                print(f"Batch skipped due to error: {e}")

            finally:
                # Clear memory
                del user_ids, item_ids, item_metadata
                torch.cuda.empty_cache()
                gc.collect()

    avg_latency = total_latency / num_batches if num_batches > 0 else 0.0
    return avg_latency

In [18]:
# baseline

latency = measure_latency(recommendation_model, test_loader)
print(f"Inference Latency: {latency:.6f} seconds")

Measuring Latency: 100%|██████████| 5107/5107 [34:25<00:00,  2.47batch/s]

Inference Latency: 0.164965 seconds


In [19]:
# sparsity = 0.3
latency = measure_latency(pruned_model, test_loader)
print(f"Inference Latency: {latency:.6f} seconds")

Measuring Latency: 100%|██████████| 5107/5107 [34:37<00:00,  2.46batch/s]

Inference Latency: 0.166595 seconds


In [21]:
# sparsity = 0.5
latency = measure_latency(pruned_model, test_loader)
print(f"Inference Latency: {latency:.6f} seconds")

Measuring Latency: 100%|██████████| 5107/5107 [34:32<00:00,  2.46batch/s]

Inference Latency: 0.166479 seconds


In [15]:
# sparsity = 0.7
latency = measure_latency(pruned_model, test_loader)
print(f"Inference Latency: {latency:.6f} seconds")

Measuring Latency: 100%|██████████| 5107/5107 [35:05<00:00,  2.43batch/s]

Inference Latency: 0.166708 seconds


#### 2. time and utilization

In [14]:
import time
import torch
import pynvml
from tqdm import tqdm
from sklearn.metrics import ndcg_score
import gc  # Garbage collector

def evaluate_model(
    model, 
    dataloader, 
    device=device, 
    k=5, 
    duration=60, 
    interval=1
):
    """
    Evaluate model performance and log GPU utilization for each GPU explicitly.

    Args:
        model (torch.nn.Module): The model to evaluate.
        dataloader (torch.utils.data.DataLoader): The DataLoader for evaluation.
        device (str): Device to run the evaluation (e.g., 'cuda').
        k (int): The value of k for recall@k and ndcg@k.
        duration (int): Duration to monitor GPU utilization.
        interval (int): Time interval to monitor GPU utilization.

    Returns:
        dict: A dictionary with all evaluation metrics.
    """
    # nvml for GPU utilization
    pynvml.nvmlInit()
    num_gpus = pynvml.nvmlDeviceGetCount()
    gpu_utilizations = {i: [] for i in range(num_gpus)}

    total_inference_time = 0.0
    total_eval_time = time.time()
    all_recall_scores = []
    all_ndcg_scores = []

    model = model.to(device)
    model.eval()

    progress_bar = tqdm(enumerate(dataloader), total=len(dataloader), desc="Evaluating", unit="batch")

    with torch.no_grad():
        for batch_idx, batch in progress_bar:
            try:
                gpu_utilization_info = []
                for gpu_index in range(num_gpus):
                    handle = pynvml.nvmlDeviceGetHandleByIndex(gpu_index)
                    utilization = pynvml.nvmlDeviceGetUtilizationRates(handle)
                    gpu_utilizations[gpu_index].append(utilization.gpu)
                    gpu_utilization_info.append(f"GPU{gpu_index}: {utilization.gpu}%")

                print(f"Batch {batch_idx} - " + ", ".join(gpu_utilization_info))

                user_ids, item_ids, metadata, targets = batch
                user_ids = user_ids.to(device).long()
                item_ids = item_ids.to(device).long()
                targets = targets.to(device)
                metadata = {
                    key: val[:, :128].to(device) for key, val in metadata.items()  
                }

                start_time = time.time()
                predictions = model(user_ids, item_ids, metadata).squeeze(-1)
                total_inference_time += time.time() - start_time

                _, top_k_indices = torch.topk(predictions, k, dim=-1)
                recall_score = (
                    (targets.unsqueeze(-1) == top_k_indices).sum(dim=-1).float().mean().item()
                )
                ndcg_score_value = ndcg_score([targets.cpu().numpy()], [predictions.cpu().numpy()], k=k)

                all_recall_scores.append(recall_score)
                all_ndcg_scores.append(ndcg_score_value)

                progress_bar.set_postfix({
                    "Batch": batch_idx,
                    "Avg Recall@k": f"{sum(all_recall_scores)/len(all_recall_scores):.4f}",
                    "Avg NDCG@k": f"{sum(all_ndcg_scores)/len(all_ndcg_scores):.4f}"
                })

            except RuntimeError as e:
                print(f"Error in batch {batch_idx}: {e}")
                continue

            finally:
                # clear memory for current batch to save CUDA memory 
                del user_ids, item_ids, metadata, predictions, targets, top_k_indices
                torch.cuda.empty_cache()  
                gc.collect()  

    avg_gpu_utilization = {
        gpu_index: sum(utilizations) / len(utilizations)
        for gpu_index, utilizations in gpu_utilizations.items()
    }

    # we are dealing with per batch
    total_eval_time = (time.time() - total_eval_time) / 5106
    average_recall = sum(all_recall_scores) / len(all_recall_scores)
    average_ndcg = sum(all_ndcg_scores) / len(all_ndcg_scores)
    total_inference_time  = total_inference_time / 8

    pynvml.nvmlShutdown()

    # Return metrics
    return {
        "Average GPU Utilization": avg_gpu_utilization,
        "Total Inference Time": total_inference_time,
        "Overall Evaluation Time": total_eval_time,
        "Recall@k": average_recall,
        "NDCG@k": average_ndcg,
    }



In [11]:
# sparsity = 0.3
results = evaluate_model(pruned_model, test_loader, device=device, k=5, duration=60, interval=1)
print("\nEvaluation Results:")
for metric, value in results.items():
    print(f"{metric}: {value}")

Evaluating:   0%|          | 0/5107 [00:00<?, ?batch/s]Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Batch 0 - GPU0: 38%, GPU1: 0%, GPU2: 0%, GPU3: 0%


Evaluating:   0%|          | 1/5107 [00:03<4:45:01,  3.35s/batch, Batch=0, Avg Recall@k=0.0000, Avg NDCG@k=0.9558]

Batch 1 - GPU0: 0%, GPU1: 35%, GPU2: 66%, GPU3: 59%


Evaluating:   0%|          | 2/5107 [00:03<2:25:22,  1.71s/batch, Batch=1, Avg Recall@k=0.0000, Avg NDCG@k=0.9010]

...

Batch 5105 - GPU0: 1%, GPU1: 46%, GPU2: 69%, GPU3: 66%


Evaluating: 100%|█████████▉| 5106/5107 [47:01<00:00,  1.83batch/s, Batch=5105, Avg Recall@k=0.0000, Avg NDCG@k=0.9558]

Batch 5106 - GPU0: 13%, GPU1: 68%, GPU2: 36%, GPU3: 61%


Evaluating: 100%|██████████| 5107/5107 [47:01<00:00,  1.81batch/s, Batch=5106, Avg Recall@k=0.0000, Avg NDCG@k=0.9558]


Evaluation Results:
Average GPU Utilization: {0: 2.2079498727237126, 1: 40.17779518308205, 2: 49.59252007049148, 3: 55.59702369297043}
Total Inference Time: 164.02077651023865
Overall Evaluation Time: 0.5528587569361147
Recall@k: 0.0
NDCG@k: 0.9557630024343363


In [11]:
# sparsity = 0.5
results = evaluate_model(pruned_model, test_loader, device=device, k=5, duration=60, interval=1)
print("\nEvaluation Results:")
for metric, value in results.items():
    print(f"{metric}: {value}")

Evaluating:   0%|          | 0/5107 [00:00<?, ?batch/s]Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Batch 0 - GPU0: 39%, GPU1: 0%, GPU2: 0%, GPU3: 0%


Evaluating:   0%|          | 1/5107 [00:03<4:34:30,  3.23s/batch, Batch=0, Avg Recall@k=0.0000, Avg NDCG@k=0.9595]

Batch 1 - GPU0: 0%, GPU1: 76%, GPU2: 66%, GPU3: 74%


Evaluating:   0%|          | 2/5107 [00:03<2:20:33,  1.65s/batch, Batch=1, Avg Recall@k=0.0000, Avg NDCG@k=0.9366]

...

Batch 5105 - GPU0: 17%, GPU1: 47%, GPU2: 42%, GPU3: 61%


Evaluating: 100%|█████████▉| 5106/5107 [45:04<00:00,  1.93batch/s, Batch=5105, Avg Recall@k=0.0000, Avg NDCG@k=0.9543]

Batch 5106 - GPU0: 0%, GPU1: 61%, GPU2: 55%, GPU3: 30%


Evaluating: 100%|██████████| 5107/5107 [45:04<00:00,  1.89batch/s, Batch=5106, Avg Recall@k=0.0000, Avg NDCG@k=0.9543]


Evaluation Results:
Average GPU Utilization: {0: 2.91090659878598, 1: 43.82514196201292, 2: 51.51909144311729, 3: 56.42157822596436}
Total Inference Time: 154.51013576984406
Overall Evaluation Time: 0.5299697018491488
Recall@k: 0.0
NDCG@k: 0.9542900547591932


In [15]:
# sparsity = 0.7
results = evaluate_model(pruned_model, test_loader, device=device, k=5, duration=60, interval=1)
print("\nEvaluation Results:")
for metric, value in results.items():
    print(f"{metric}: {value}")

Evaluating:   0%|          | 0/5107 [00:00<?, ?batch/s]

Batch 0 - GPU0: 0%, GPU1: 0%, GPU2: 0%, GPU3: 0%


Evaluating:   0%|          | 1/5107 [00:02<2:55:22,  2.06s/batch, Batch=0, Avg Recall@k=0.0000, Avg NDCG@k=0.9582]

Batch 1 - GPU0: 0%, GPU1: 68%, GPU2: 5%, GPU3: 66%


Evaluating:   0%|          | 2/5107 [00:02<1:40:15,  1.18s/batch, Batch=1, Avg Recall@k=0.0000, Avg NDCG@k=0.9611]

...

Batch 5105 - GPU0: 10%, GPU1: 14%, GPU2: 39%, GPU3: 24%


Evaluating: 100%|█████████▉| 5106/5107 [45:54<00:00,  1.89batch/s, Batch=5105, Avg Recall@k=0.0000, Avg NDCG@k=0.9588]

Batch 5106 - GPU0: 0%, GPU1: 27%, GPU2: 53%, GPU3: 37%


Evaluating: 100%|██████████| 5107/5107 [45:54<00:00,  1.85batch/s, Batch=5106, Avg Recall@k=0.0000, Avg NDCG@k=0.9588]


Evaluation Results:
Average GPU Utilization: {0: 2.0867436851380456, 1: 39.55335813589191, 2: 47.43861366751518, 3: 54.50695124339143}
Total Inference Time: 154.75543150305748
Overall Evaluation Time: 0.5395586581684028
Recall@k: 0.0
NDCG@k: 0.9587798260050383


#### 3. throughput

In [12]:

from tqdm import tqdm
def measure_throughput(model, dataloader, device=device):
    import time
    import torch

    model = model.to(device)
    model.eval()

    total_samples = 0  
    total_inference_time = 0.0  

    with torch.no_grad():
        for batch in tqdm(dataloader, desc="Measuring Throughput", unit="batch"):
            batch_size = batch[0].size(0) 
            total_samples += batch_size

            user_ids, item_ids, metadata, _ = batch
            user_ids = user_ids.to(device).long()
            item_ids = item_ids.to(device).long()
            metadata = {key: val[:, :128].to(device) for key, val in metadata.items()}  

            start_time = time.time()
            _ = model(user_ids, item_ids, metadata)
            total_inference_time += time.time() - start_time

    throughput = total_samples / total_inference_time if total_inference_time > 0 else 0.0
    return throughput

In [20]:
# sparsity = 0.3
throughout = measure_throughput(pruned_model, test_loader)

Measuring Throughput: 100%|██████████| 5107/5107 [14:14<00:00,  5.98batch/s]


In [21]:
throughout

357.5351639926866

In [13]:
# sparsity = 0.5
throughput = measure_throughput(pruned_model, test_loader)
throughput

Measuring Throughput: 100%|██████████| 5107/5107 [14:16<00:00,  5.96batch/s]


323.349409444434

In [15]:
# sparsity = 0.7
throughput = measure_throughput(pruned_model, test_loader)
throughput

Measuring Throughput: 100%|██████████| 5107/5107 [14:07<00:00,  6.03batch/s]


331.05700596515663